In [ ]:
import os
import sys
import torch
need_pytorch3d=False
try:
    import pytorch3d
except ModuleNotFoundError:
    need_pytorch3d=True
if need_pytorch3d:
    if torch.__version__.startswith("1.10.") and sys.platform.startswith("linux"):
        # We try to install PyTorch3D via a released wheel.
        pyt_version_str=torch.__version__.split("+")[0].replace(".", "")
        version_str="".join([
            f"py3{sys.version_info.minor}_cu",
            torch.version.cuda.replace(".",""),
            f"_pyt{pyt_version_str}"
        ])
        !pip install fvcore iopath
        !pip install --no-index --no-cache-dir pytorch3d -f https://dl.fbaipublicfiles.com/pytorch3d/packaging/wheels/{version_str}/download.html
    else:
        # We try to install PyTorch3D from source.
        !curl -LO https://github.com/NVIDIA/cub/archive/1.10.0.tar.gz
        !tar xzf 1.10.0.tar.gz
        os.environ["CUB_HOME"] = os.getcwd() + "/cub-1.10.0"
        !pip install 'git+https://github.com/facebookresearch/pytorch3d.git@stable'
# Set up starter code
!git clone https://github.com/learning3d/assignment1.git
!mv assignment1/* .
!pip install -r requirements.txt

     |████████████████████████████████| 55 kB 2.4 MB/s 
     |████████████████████████████████| 596 kB 10.9 MB/s 
  Created wheel for fvcore: filename=fvcore-0.1.5.post20220119-py3-none-any.whl size=65267 sha256=e424b0e4d720a8d1f5b9efa56e230514a1844e81de235ec015faab83c0f871cd
  Stored in directory: /root/.cache/pip/wheels/f3/b8/eb/61ed840f80d7198725bc061872b6019a7b3e9db4dbadf68083
Successfully built fvcore
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
Looking in links: https://dl.fbaipublicfiles.com/pytorch3d/packaging/wheels/py37_cu111_pyt1100/download.html
     |████████████████████████████████| 44.7 MB 1.5 MB/s 
Cloning into 'assignment1'...
remote: Enumerating objects: 46, done.
remote: Counting objects: 100% (46/46), done.
remote: Compressing objects: 100% (36/36), done.
remote: Total 46 (delta 9), reused 40 (delta 7), pack-reused 0
Unpacking objects: 100% (46/46), done.
     |██

P5.1 3 point cloud rendering, to generate, run the follwoing 5 blocks 

In [ ]:
import argparse
import pickle

import matplotlib.pyplot as plt
import mcubes
import numpy as np
import pytorch3d
import torch
import pytorch3d
import pytorch3d.io
from pytorch3d.vis.plotly_vis import plot_scene
from tqdm.auto import tqdm

import starter.utils
from starter.utils import get_device, get_mesh_renderer, get_points_renderer


def load_rgbd_data(path="data/rgbd_data.pkl"):
    with open(path, "rb") as f:
        data = pickle.load(f)
    return data

'''
render = "point_cloud"
output_path = "P5.jpg"
num_samples = 100
image_size = 256


plt.imsave(output_path,image)
'''
#
data_p5 = load_rgbd_data()
print(data_p5.keys())
image_size = 256
background_color=(1, 1, 1)
device=None

if device is None:
  device = get_device()

dict_keys(['rgb1', 'mask1', 'depth1', 'rgb2', 'mask2', 'depth2', 'cameras1', 'cameras2'])


In [ ]:
def unproject_depth_image(image, mask, depth, camera):
    """
    Unprojects a depth image into a 3D point cloud.

    Args:
        image (torch.Tensor): A square image to unproject (S, S, 3).
        mask (torch.Tensor): A binary mask for the image (S, S).
        depth (torch.Tensor): The depth map of the image (S, S).
        camera: The Pytorch3D camera to render the image.
    
    Returns:
        points (torch.Tensor): The 3D points of the unprojected image (N, 3).
        rgba (torch.Tensor): The rgba color values corresponding to the unprojected
            points (N, 4).
    """
    device = camera.device
    assert image.shape[0] == image.shape[1], "Image must be square."
    image_shape = image.shape[0]
    ndc_pixel_coordinates = torch.linspace(1, -1, image_shape)
    Y, X = torch.meshgrid(ndc_pixel_coordinates, ndc_pixel_coordinates)
    xy_depth = torch.dstack([X, Y, depth])
    points = camera.unproject_points(
        xy_depth.to(device), in_ndc=False, from_ndc=False, world_coordinates=True,
    )
    points = points[mask > 0.5]
    rgb = image[mask > 0.5]
    rgb = rgb.to(device)

    # For some reason, the Pytorch3D compositor does not apply a background color
    # unless the pointcloud is RGBA.
    alpha = torch.ones_like(rgb)[..., :1]
    rgb = torch.cat([rgb, alpha], dim=1)

    return points, rgb

In [ ]:
pt1,rgb1 = unproject_depth_image(torch.Tensor(data_p5['rgb1']), torch.Tensor(data_p5['mask1']), 
                torch.Tensor(data_p5['depth1']), data_p5['cameras1'])
pt2,rgb2 = unproject_depth_image(torch.Tensor(data_p5['rgb2']), torch.Tensor(data_p5['mask2']),
                torch.Tensor(data_p5['depth2']), data_p5['cameras2'])
pt1P = pytorch3d.structures.Pointclouds(
    points=torch.Tensor(pt1).unsqueeze(0),
    features=torch.Tensor(rgb1).unsqueeze(0),
).to(device)

pt2P = pytorch3d.structures.Pointclouds(
    points=torch.Tensor(pt2).unsqueeze(0),
    features=torch.Tensor(rgb2).unsqueeze(0),
).to(device)

#merged pointcloud
pt3 = torch.cat((pt1, pt2), 0)
rgb3 = torch.cat((rgb1, rgb2), 0)
pt3P = pytorch3d.structures.Pointclouds(
    points=torch.Tensor(pt3).unsqueeze(0),
    features=torch.Tensor(rgb3).unsqueeze(0),
).to(device)

/usr/local/lib/python3.7/dist-packages/torch/functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ../aten/src/ATen/native/TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]


In [ ]:
def gif_generate(pt_var,name_var):
    num_views = 15
    renderer = get_points_renderer(image_size=image_size, device=device)
    lights = pytorch3d.renderer.PointLights(location=[[0, 0.0, 6.0]], device=device,)
    my_images=[]
    for i in range(num_views):
      R, T = pytorch3d.renderer.look_at_view_transform(dist=6, elev=0, azim=-180+360/num_views*i)
      #print('R',R,'T',T)
      #temp_R=R
      #for adjust camera R
      temp_R=R.squeeze(0).mm(torch.tensor([[1,0,0],[0,-1,0],[0,0,1]]).float()).unsqueeze(0)
      cameras = pytorch3d.renderer.FoVPerspectiveCameras(R=temp_R, T=T, device=device)
      images_gif = renderer(pt_var, cameras=cameras, lights=lights)
      #temp=images_gif.cpu().detach().numpy()
      #my_images.append(temp)
      
      for j, image in enumerate(images_gif):
          #print(image.shape)
          temp=image.cpu().detach().numpy()
          my_images.append(temp)
    import imageio
    imageio.mimsave(name_var, my_images, fps=num_views)

    return 0

In [ ]:
gif_generate(pt1P,'P5_pc1.gif')
gif_generate(pt2P,'P5_pc2.gif')
gif_generate(pt3P,'P5_pc3.gif')

P5.2 Render Torus, run the following codeblock

In [ ]:
import argparse
import pickle

import matplotlib.pyplot as plt
import mcubes
import numpy as np
import pytorch3d
import torch

from starter.utils import get_device, get_mesh_renderer, get_points_renderer
device=None
if device is None:
  device = get_device()


num_samples=100
phi = torch.linspace(0, 2*np.pi, num_samples)
theta = torch.linspace(0, 2*np.pi, num_samples)
# Densely sample phi and theta on a grid
Phi, Theta = torch.meshgrid(phi, theta)
R_tor=2
r_tor=1
x = (R_tor+r_tor*torch.cos(Theta)) * torch.cos(Phi)
y = (R_tor+r_tor*torch.cos(Theta)) * torch.sin(Phi)
z = r_tor*torch.sin(Theta)
image_size = 256

points = torch.stack((x.flatten(), y.flatten(), z.flatten()), dim=1)
color = (points - points.min()) / (points.max() - points.min())

sphere_point_cloud = pytorch3d.structures.Pointclouds(
    points=[points], features=[color],
).to(device)

#gif_generate(sphere_point_cloud,'P5_2.gif')
'''
cameras = pytorch3d.renderer.FoVPerspectiveCameras(T=[[0, 0, 6]], device=device)
renderer = get_points_renderer(image_size=image_size, device=device)
rend = renderer(sphere_point_cloud, cameras=cameras)
plt.imshow(rend[0, ..., :3].cpu().numpy())
'''
num_views = 15
R_gif, T_gif = pytorch3d.renderer.look_at_view_transform(
    dist=10,
    elev=3,
    azim=np.linspace(-180, 180, num_views, endpoint=False),
)
print("R_gif", R_gif.shape)
print("T_gif", T_gif.shape)
many_cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R_gif,
    T=T_gif,
    device=device
)
lights = pytorch3d.renderer.PointLights(location=[[0, 0, -3]], device=device)
renderer = get_points_renderer(image_size=image_size, device=device)
images_gif = renderer(sphere_point_cloud.extend(num_views), cameras=many_cameras, lights=lights)
my_images=[]
for i, image in enumerate(images_gif):
    temp=image.cpu().detach().numpy()
    my_images.append(temp)
    print(type(temp))
import imageio
imageio.mimsave('P52.gif', my_images, fps=5)

#'''



P5.3 Render torus through implicit function
&
P6 Render complex implict function

In [ ]:
import argparse
import pickle

import matplotlib.pyplot as plt
import mcubes
import numpy as np
import pytorch3d
import torch
import math

from starter.utils import get_device, get_mesh_renderer, get_points_renderer
image_size=256
voxel_size=64
device=None

if device is None:
      device = get_device()
min_value = -5
max_value = 5
X, Y, Z = torch.meshgrid([torch.linspace(min_value, max_value, voxel_size)] * 3)

#voxels = (torch.sqrt(X ** 2 + Y ** 2)-4)**2 + Z ** 2 - 1

#To render complexed implict function, delet comment of next line
voxels = X**2+Y**2-(torch.log10(Z+2.2))**2-0.02

vertices, faces = mcubes.marching_cubes(mcubes.smooth(voxels), isovalue=0)


vertices = torch.tensor(vertices).float()
faces = torch.tensor(faces.astype(int))

vertices = (vertices / voxel_size) * (max_value - min_value) + min_value
textures = (vertices - vertices.min()) / (vertices.max() - vertices.min())
textures = pytorch3d.renderer.TexturesVertex(vertices.unsqueeze(0))

mesh = pytorch3d.structures.Meshes([vertices], [faces], textures=textures).to(
    device
  )
lights = pytorch3d.renderer.PointLights(location=[[0, 0.0, -4.0]], device=device,)
renderer = get_mesh_renderer(image_size=image_size, device=device)

num_views = 15
R_gif, T_gif = pytorch3d.renderer.look_at_view_transform(
    dist=10,
    elev=3,
    azim=np.linspace(-180, 180, num_views, endpoint=False),
)
many_cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R_gif,
    T=T_gif,
    device=device
)
images_gif = renderer(mesh.extend(num_views), cameras=many_cameras, lights=lights)
my_images=[]
for i, image in enumerate(images_gif):
    temp=image.cpu().detach().numpy()
    my_images.append(temp)
    print(type(temp))
import imageio
imageio.mimsave('P53.gif', my_images, fps=5)




(Extra Credit) 7. Sampling Points on Meshes 
To generate, just run the code and adjust k_v and
gif_name

In [ ]:
import argparse
import matplotlib.pyplot as plt
import pytorch3d
import torch
import random
import math
import numpy

from starter.utils import get_device, get_mesh_renderer, load_cow_mesh


def render_cow(
    cow_path="data/cow.obj", image_size=256, color=[0.7, 0.7, 1], device=None,
):
    
    if device is None:
        device = get_device()

    renderer = get_mesh_renderer(image_size=image_size)

    vertices, faces = load_cow_mesh(cow_path)

    #print('vertices shape',vertices.shape)
    #print('faces shape',faces.shape)
    #print('vertices ',vertices[0])
    #print('faces ',faces[0])

    list_area=[]
    #claculate triangle surface in 3d
    for i in range(faces.shape[0]):
      a=vertices[faces[i][0]]
      b=vertices[faces[i][1]]
      c=vertices[faces[i][2]]
      ab=a-b
      ac=a-c
      area=abs(torch.dot(ab,ac)*0.5)
      list_area.append(area)
    list_sum=sum(list_area)
    list_prop=[]
    for j in list_area:
      list_prop.append(j/list_sum)
    #print(len(list_prop),list_prop[0])

    list_choice=[]
    #
    #
    k_v=10000
    gif_name="P7_10000.gif"
    # 
    #
    list_choice=random.choices(
    faces,
    weights=list_prop,
    k=k_v)
    #print('list_choice',len(list_choice))
    points_p=torch.zeros([len(list_choice),3])
    #'''
    #Barycentric coordinate
    for k in range(len(list_choice)):
      alpha1 = random.random()
      alpha2 = math.sqrt(alpha1)
      alpha3 = 1-alpha1-alpha2
      p1=vertices[list_choice[k][0]]
      p2=vertices[list_choice[k][1]]
      p3=vertices[list_choice[k][2]]
      xp=alpha1*p1[0]+alpha2*p2[0]+alpha3*p3[0]
      yp=alpha1*p1[1]+alpha2*p2[1]+alpha3*p3[1]
      cp=alpha1*p1[2]+alpha2*p2[2]+alpha3*p3[2]
      points_p[k,0]=xp
      points_p[k,1]=yp
      points_p[k,2]=cp
    #'''
    #color = torch.tensor([0.7, 0.7, 1])
    color = (points_p - points_p.min()) / (points_p.max() - points_p.min())
    print("points_p shape",points_p.shape)
    sample_point_cloud = pytorch3d.structures.Pointclouds(
    points=[points_p], features=[color],
    ).to(device)

    num_views = 15
    R_gif, T_gif = pytorch3d.renderer.look_at_view_transform(
    dist=3,
    elev=0,
    azim=np.linspace(-180, 180, num_views, endpoint=False),
    )

    # Prepare the camera:
    many_cameras = pytorch3d.renderer.FoVPerspectiveCameras(
    R=R_gif,
    T=T_gif,
    device=device
    )

    # Place a point light in front of the cow.
    lights = pytorch3d.renderer.PointLights(location=[[0, 0, -3]], device=device)
    renderer = get_points_renderer(image_size=image_size, device=device)
    images_gif = renderer(sample_point_cloud.extend(num_views), cameras=many_cameras, lights=lights)
    my_images=[]
    for i, image in enumerate(images_gif):
        temp=image.cpu().detach().numpy()
        my_images.append(temp)
        #print(type(temp))
    
    import imageio
    imageio.mimsave(gif_name, my_images, fps=5)
    
    return 0



cow_path="data/cow.obj"
#output_path="cow_render_bonuous.jpg"
image_size=256

image = render_cow(cow_path=cow_path, image_size=image_size)
#plt.imsave(args.output_path, image)

points_p shape torch.Size([10000, 3])
